In [ ]:
#!pip install -q -U bitsandbytes
!pip install -q -U git+https://github.com/huggingface/transformers.git
#!pip install -q -U git+https://github.com/huggingface/peft.git
!pip install -q -U git+https://github.com/huggingface/accelerate.git
!pip install -q -U datasets
!pip install xformers

  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 268.8/268.8 kB 5.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 41.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 55.1 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 519.3/519.3 kB 7.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.3/115.3 kB 7.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 10.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 11.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 167.0/167.0 MB 6.7 MB/s eta 0:00:00


In [ ]:
from huggingface_hub import notebook_login

notebook_login()

In [ ]:
from transformers import AutoTokenizer,AutoModelForCausalLM
from datasets import load_dataset

In [ ]:
#print(args.model_path)
model = AutoModelForCausalLM.from_pretrained("bigscience/bloomz-560m")
tokenizer = AutoTokenizer.from_pretrained("bigscience/bloomz-560m")

In [ ]:
tokenizer.pad_token_id = 7

In [ ]:
data = load_dataset("json", data_files='/content/imran_chi_fyp.json')

Extracting data files:   0%|          | 0/1 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

In [ ]:
# optimized for RTX 4090. for larger GPUs, increase some of these?
MICRO_BATCH_SIZE = 4  # this could actually be 5 but i like powers of 2
BATCH_SIZE = 128
MAX_STEPS = None
GRADIENT_ACCUMULATION_STEPS = BATCH_SIZE // MICRO_BATCH_SIZE
EPOCHS = 3  # we don't always need 3 tbh
LEARNING_RATE = 3e-4  # the Karpathy constant
CUTOFF_LEN = 256  # 256 accounts for about 96% of the data
LORA_R = 8
LORA_ALPHA = 16
LORA_DROPOUT = 0.05
VAL_SET_SIZE = 0.01

In [ ]:

def generate_prompt(data_point):
    # sorry about the formatting disaster gotta move fast
    if data_point["input"]:
        return f""" Below is an instruction that describes a task, paired with an input that provides further context. Write a response that appropriately completes the request.
### Instruction:
{data_point["instruction"]}

### Input:
{data_point["input"]}

### Response:
{data_point["output"]}"""
    else:
        return f""" Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
{data_point["instruction"]}

### Response:
{data_point["output"]}"""


def tokenize(prompt):
    # there's probably a way to do this with the tokenizer settings
    # but again, gotta move fast
    result = tokenizer(
        prompt,
        truncation=True,
        max_length=CUTOFF_LEN + 1,
        padding="max_length",
    )
    return {
        "input_ids": result["input_ids"][:-1],
        "attention_mask": result["attention_mask"][:-1],
    }


def generate_and_tokenize_prompt(data_point):
    # This function masks out the labels for the input,
    # so that our loss is computed only on the response.
    user_prompt = (
        (
            f""" Below is an instruction that describes a task, paired with an input that provides further context. Write a response that appropriately completes the request.

### Instruction:
{data_point["instruction"]}

### Input:
{data_point["input"]}

### Response:
"""
        )
        if data_point["input"]
        else (
            f""" Below is an instruction that describes a task. Write a response that appropriately completes the request.
### Instruction:
{data_point["instruction"]}

### Response:
"""
        )
    )
    len_user_prompt_tokens = (
        len(
            tokenizer(
                user_prompt,
                truncation=True,
                max_length=CUTOFF_LEN + 1,
            )["input_ids"]
        )
        - 1
    )  # no eos token
    full_tokens = tokenizer(
        user_prompt + data_point["output"],
        truncation=True,
        max_length=CUTOFF_LEN + 1,
        padding="max_length",
    )["input_ids"][:-1]
    return {
        "input_ids": full_tokens,
        "labels": [-100] * len_user_prompt_tokens
        + full_tokens[len_user_prompt_tokens:],
        "attention_mask": [1] * (len(full_tokens)),
    }


if VAL_SET_SIZE > 0:
    train_val = data["train"].train_test_split(
        test_size=VAL_SET_SIZE, shuffle=True, seed=42
    )
    train_data = train_val["train"].shuffle().map(generate_and_tokenize_prompt)
    val_data = train_val["test"].shuffle().map(generate_and_tokenize_prompt)
else:
    train_data = data["train"].shuffle().map(generate_and_tokenize_prompt)
    val_data = None

Map:   0%|          | 0/1769 [00:00<?, ? examples/s]

Map:   0%|          | 0/18 [00:00<?, ? examples/s]

In [ ]:
import transformers
trainer = transformers.Trainer(
    model=model,
    train_dataset=train_data,
    eval_dataset=val_data,
    args=transformers.TrainingArguments(
        per_device_train_batch_size=2,
        gradient_accumulation_steps=GRADIENT_ACCUMULATION_STEPS,
        warmup_steps=100,
        max_steps=300,
        #num_train_epochs=5,
        learning_rate=3e-4 ,
        #weight_decay=0.01,
        fp16=True,
        logging_steps=10,
        output_dir='bloom_p560m_5',
        #push_to_hub=True


    ),

    data_collator=transformers.DataCollatorForLanguageModeling(tokenizer, mlm=False)
)

print("\n ========== train...========= \n")

trainer.train()

You're using a BloomTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.



 ========== train...========= 



KeyboardInterrupt: ignored

In [ ]:
trainer.push_to_hub()
path = 'bloom_p560m_5'
#trainer.save_model(path)
tokenizer.push_to_hub(path)

Upload file pytorch_model.bin:   0%|          | 1.00/2.08G [00:00<?, ?B/s]

Upload file runs/May28_06-51-56_11b6804bfda1/1685256722.265447/events.out.tfevents.1685256722.11b6804bfda1.296…

Upload file training_args.bin:   0%|          | 1.00/3.81k [00:00<?, ?B/s]

Upload file runs/May28_06-51-56_11b6804bfda1/events.out.tfevents.1685256722.11b6804bfda1.296.0:   0%|         …

To https://huggingface.co/Imran1/bloom_p560m_5
   2d98ad4..90185c0  main -> main

   2d98ad4..90185c0  main -> main

To https://huggingface.co/Imran1/bloom_p560m_5
   90185c0..a4cb8b6  main -> main

   90185c0..a4cb8b6  main -> main



Upload 1 LFS files:   0%|          | 0/1 [00:00<?, ?it/s]

tokenizer.json:   0%|          | 0.00/14.5M [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/Imran1/bloom_p560m_5/commit/2676e959a58b857b0ea367bf3232c4389331e401', commit_message='Upload tokenizer', commit_description='', oid='2676e959a58b857b0ea367bf3232c4389331e401', pr_url=None, pr_revision=None, pr_num=None)

In [ ]:
path = 'Imran1/bloom_p560m_5'
from transformers import pipeline
pipe = pipeline('text-generation',model=path, tokenizer=path,device=0)

In [ ]:
def generate_prompt(instruction, input=None):
    if input:
        return f"""Below is an instruction that describes a task, paired with an input that provides further context. Write a response that appropriately completes the request.
### Instruction:
{instruction}
### Input:
{input}
### Response:"""
    else:
        return f"""Below is an instruction that describes a task. Write a response that appropriately completes the request.
### Instruction:
{instruction}
### Response:"""

In [ ]:
text = """
چې ناظر د ساده رويو پۀ رخسار شم
"""
prompt = generate_prompt(text)
new = pipe(prompt,
           max_length=200,
           do_sample=True,
           top_k=400,
           top_p=0.7,
           temperature=0.9,
           #repetition_penalty=True,
          )


print(new[0]['generated_text'])

Below is an instruction that describes a task. Write a response that appropriately completes the request.
### Instruction:

چې ناظر د ساده رويو پۀ رخسار شم

### Response:
پۀ دا شمع, پروانه غوندې, نثار شم

کۀ هر څو پۀ صبر زړۀ ټولوم, نۀ شي
بې اختياره لکه موم ويلې پۀ نار شم

غنچه خلۀ چې په خبرو راته وا کا
د نرګس پۀ څير کوز ګورم, شرمسار شم

چې يې شونډې تبسم تازه نګار کا
باندې زۀ لکه سپند سوو ته تيار شم

ځان جهان مې هس�
